# EPUSP - Hypergraph representation - v.12.2022

EPUSP - Hypergraph representation - v.12.2022 Author: Waldemir Cambiucci Data: Dec 29th, 2022

Description:  jupyter notebook particionamento aleatório não otimizado de circuitos de calibração.

Circuitos selecionados:

ae_indep_qiskit_10.qasm					
qft_indep_qiskit_10.qasm					
qpeexact_indep_qiskit_10.qasm					
ghz_indep_qiskit_10.qasm

ae_indep_qiskit_50.qasm					
qft_indep_qiskit_50.qasm					
qpeexact_indep_qiskit_50.qasm					
ghz_indep_qiskit_50.qasm					

ae_indep_qiskit_100.qasm					
qft_indep_qiskit_100.qasm					
qpeexact_indep_qiskit_100.qasm					
ghz_indep_qiskit_100.qasm

In [43]:
def get_vertices_from_gate(line):    
    split1 = line.split(" ")      
    split2 = split1[1].split(",")
    node1 = split2[0]
    node2 = split2[1] 
    node2 = node2[0:len(node2)-1]
    tupla_str = (node1),(node2)    
    return tupla_str

In [44]:
def get_nqubits_qreg(line): 
    ls = line.split(' ')
    lb = ls[1].split('[')
    ln = lb[1].split(']')
    nq = int(ln[0])
    return nq

In [45]:
def get_label_qreg(line):   
    ls = line.split(' ')
    lb = ls[1].split('[')
    label = lb[0]    
    return label

In [46]:
def convert_qasm_in_extended_hypergraph(qasm_str):  
    
    # creating the hypergraph from qasm
    hypergraph_from_qasm = {
    'nodes': [],
    'edges': [],
    'gates': [],
    'ebits': [],
    'qreg_labels': [],
    'qreg_qubits': [],
    'prelude': [],
    'epilogo': []
    }
      
    #=========================================================================
    # Creating nodes and qreg_labels from qreg instructions in qasm file
    # 
    for line in qasm_str.splitlines():
        
        if any([line.startswith(t) for t in ['qreg']]): 
            
            # for a specific qreg label, save the label in list qreg_labels
            str_label_qreg = get_label_qreg(line)
            hypergraph_from_qasm['qreg_labels'].append(str(str_label_qreg))
           
            # for the number of qubits in the specific qreg, 
            # create a number of nodes in the hyper grapph
            int_qubits_qreg = get_nqubits_qreg(line)
            hypergraph_from_qasm['qreg_qubits'].append(int_qubits_qreg)
            
            for i in range(int_qubits_qreg):
                str_node = str_label_qreg + "[" + str(i) + "]"
                hypergraph_from_qasm['nodes'].append(str_node)
            
    #=========================================================================
    
    preludes = 0
    epilog = 0
    
    # creating tuplas of 2-qubits gates in the circuit
    for line in qasm_str.splitlines():
        
        if any([line.startswith(t) for t in ['OPENQASM', 'include', 'qreg', 'creg', '//']]):            
            hypergraph_from_qasm['prelude'].append(line)
            
        elif line.startswith('cx'):            
            vertices_str = get_vertices_from_gate(line)
            hypergraph_from_qasm['edges'].append(vertices_str)
            hypergraph_from_qasm['gates'].append('cx')
            
        elif line.startswith('cz'):            
            vertices_str = get_vertices_from_gate(line)
            hypergraph_from_qasm['edges'].append(vertices_str)
            hypergraph_from_qasm['gates'].append('cz')
            
        elif line.startswith('cp'):            
            vertices_str = get_vertices_from_gate(line)
            hypergraph_from_qasm['edges'].append(vertices_str)
            hypergraph_from_qasm['gates'].append('cp')
            
        elif line.startswith('swap'):            
            vertices_str = get_vertices_from_gate(line)
            hypergraph_from_qasm['edges'].append(vertices_str)    
            hypergraph_from_qasm['gates'].append('swap')
            
        elif line.startswith('measure'): 
            hypergraph_from_qasm['epilogo'].append(line)
     
    return hypergraph_from_qasm 

In [47]:
def extended_hypergraph_partition_by_connections(hg,nparts):    
                
    partitionsList=[]
    
    # creating the hypergraph from qasm
    aux_hg = {
        'nodes': [],
        'edges': [],
        'gates': [],
        'ebits': [],
        'qreg_labels': [],
        'qreg_qubits': [],
        'prelude': [],
        'epilogo': []
    }  

    total_nodes = len(hg['nodes'])
    total_edges = len(hg['edges'])
    total_gates = len(hg['gates'])
    
    balance_nodes = int(total_nodes / nparts)
    
    # index for control of partitions
    w, h = 2, nparts
    index_partition = [[0 for x in range(w)] for y in range(h)] 

    # --------------------------------------------------------------------------------
    # preparing partition index 
    for i in range(nparts):   
        
        # initial index for the partition
        index_partition[i][0] = i*balance_nodes    
        
        # final index for the partition
        index_partition[i][1] = index_partition[i][0] + balance_nodes - 1        
        
    # --------------------------------------------------------------------------------
    # repeat number of partition times    
    for p in range(nparts):
        
        print("# Creating segment: " + str(p+1))
        
        # adding nodes for the segment p
        c = 0        
        for node in hg['nodes']:
            if(c >= index_partition[p][0]) and (c <= index_partition[p][1]):
                aux_hg['nodes'].append(node)        
            c = c + 1
            
        # adding qreg_labels for the segment p
        for qreg_label in hg['qreg_labels']:
            aux_hg['qreg_labels'].append(qreg_label)
            
        # adding qreg_qubits for the segment p
        for qreg_qubit in hg['qreg_qubits']:
            aux_hg['qreg_qubits'].append(qreg_qubit)
            
        # adding prelude for the segment p
        for pr in hg['prelude']:
            aux_hg['prelude'].append(pr)
            
        # adding epilogo for the segment p
        for ep in hg['epilogo']:
            aux_hg['epilogo'].append(ep)            
            
        # adding edges for the segment p
        for edge in hg['edges']:
            aux_hg['edges'].append(edge)               
        
        # adding gates for the segment p
        for gate in hg['gates']:
            aux_hg['gates'].append(gate)
            
        # record of sub-segment created
        print("\naux_hg: ", aux_hg)

        # saving the record sub-segment in the list
        partitionsList.append(aux_hg)    
        
        aux_hg = {
            'nodes': [],
            'edges': [],
            'gates': [],
            'ebits': [],
            'qreg_labels': [],
            'qreg_qubits': [],
            'prelude': [],
            'epilogo': []
        }
            
    return partitionsList

In [48]:
def statistics_from_qasm(qasm_str, p, circuit_file):
    
    # string with statistics of return
    # format: Circuit name + '\t' + n + '\t' + e + '\t' + o + '\t' + r + '\t' + p + '\t' + circuit_file
    #
    str_statistics = circuit_file
    
    # number of ebits
    e = 0
    # number of operations
    o = 0    
    # relation between e and o
    r = 0

    preludes = 0
    measure = 0
    barrier = 0
    
    nu1 = 0 
    nu2 = 0
    nu3 = 0
    
    # -------------------------------------------------------------------------------------
    #
    for line in qasm_str.splitlines():
        
        if any([line.startswith(t) for t in ['OPENQASM', 'include', 'qreg', 'creg', '//']]):            
            preludes = preludes + 1
            
        if line.startswith('measure'): 
            measure = measure + 1
            
        if line.startswith('barrier'): 
            barrier = barrier + 1
            
        if (line.startswith('cx')) or (line.startswith('cp(')) or (line.startswith('cz')) or (line.startswith('swap')): 
            e = e + 1
            o = o + 1
           
        if (line.startswith('u(')): 
            nu1 = nu1 + 1
            o = o + 1

        if (line.startswith('u2(')): 
            nu2 = nu2 + 1
            o = o + 1

        if (line.startswith('u3(')): 
            nu3 = nu3 + 1
            o = o + 1

        if (line.startswith('h ')) or (line.startswith('x ')) or (line.startswith('t ')): 
            o = o + 1            
                
    # -------------------------------------------------------------------------------------

    # calculating relation between ebits and operations
    r = e / o
    print('r: ' + str(r))
    
    nqubits1 = circuit_file.split('.')[0]
    nqubits2 = nqubits1.split('_')[5]
    n = int(nqubits2)
    
    print('n: ' + str(n))
    
    cn = circuit_file.split('_')
    circuit_name = cn[2] + "_" + str(n)
    
    print('circuit_name: ' + circuit_name)
    
    str_statistics = circuit_name + '\t' + str(n) + '\t' + str(e) + '\t' + str(o) + '\t' + str(r) + '\t' + str(p) + '\t' + circuit_file + '\n'

    # returning statistics for the circuit
    return str_statistics 

In [49]:
def valid_operation_for_this_segment(qasm_nodes,qubit1,qubit2):
    test1 = (str(qubit1) in qasm_nodes)
    test2 = (str(qubit2) in qasm_nodes)    
    if (not test1) and (not test2):
        flag = False
    else: 
        flag = True    
    return flag

In [50]:
def convert_extended_hypergraph_in_qasm(param_hg): 

    print('\n')
    print(param_hg)
    print('\n')
    
    qasm_nodes = ""
    for node in param_hg['nodes']:
        qasm_nodes = qasm_nodes + "\t" + str(node)
        
    qasm_epilogo = ""
    for item in param_hg['epilogo']:
        qasm_epilogo = qasm_epilogo + item + "\n"
    
    qasm_prelude = ""
    for item in param_hg['prelude']:
        qasm_prelude = qasm_prelude + item + "\n"
        
    # adding edges for this hypergraph
    i = 0
    qasm_circ = ""
    qasm_line = ""   
    
    for edge in param_hg['edges']:       
        qubit1 = edge[0]
        qubit2 = edge[1]
        gate = str(param_hg['gates'][i])       
        
        if ( valid_operation_for_this_segment(qasm_nodes,qubit1,qubit2) ):
            # creating the qasm line for the circuit
            qasm_line = gate  + " " +  qubit1 + "," + qubit2 + ";\n"
            qasm_circ = qasm_circ + qasm_line
        
        i = i + 1

    # creating the qasm string
    qasm_str = qasm_prelude + qasm_circ + qasm_epilogo
   
    return qasm_str

In [54]:
def create_qasm_file_from_partition(index_partition, circuit_folder, circuit_file, qc_qasm,nparts, hg, kfolder):

    # file name for the current partition
    qasm_file_from_partition = "p" + str(index_partition) + "_k" + str(nparts) + "_" + circuit_file   
        
    # creating the qasm file based in the current hg    
    with open(circuit_folder + "\\" + kfolder + "\\" + qasm_file_from_partition, 'w') as sp:  

        for line in qc_qasm.splitlines():

            if any([line.startswith(t) for t in ['OPENQASM', 'include', '//']]):  
                sp.write(line + '\n') 

            elif any([line.startswith(t) for t in ['qreg', 'creg']]):  
                sp.write(line + '\n') 

            elif any([line.startswith(t) for t in ['barrier']]):
                print("don not save barriers tag.")

            else:      
                #----------------------------------
                valid_node = False
                for node in hg['nodes']:   
                    if ( str(node) in line ):
                        valid_node = True
                if(valid_node):
                    sp.write(line + '\n')
                #----------------------------------

        # closing split file
        sp.close()      
   
    # -----------------------------------------------------
    return qasm_file_from_partition

In [63]:
from qiskit import QuantumCircuit

def random_partition_by_k(nparts):    

    print('def: run_Random_Partition_by_k')
    print('Starting process for ' + str(nparts) + ' partitions.\n')

    reg_partition_statistics = {
        'ni': int,
        'ei': int,
        'oi': int,
        'ri': int,
        'pi': int
    }    
    nreg = 5
    index_partition = [[0 for x in range(nreg)] for y in range(nparts)] 

    # Folder of circuit files for calibration.
    circuit_folder = 'balanced_partition'
    
    # log file for results
    kfolder = "k" + str(nparts)
    log_file = "log_file_" + kfolder + ".log"


    # considering small circuits for k = 2, 3, 5
    if (nparts <= 5):
        # list of circuit files for calibration with 10, 50 and 100 qubits
        circuit_files = [
                        'ae_indep_qiskit_10.qasm',
                        'qft_indep_qiskit_10.qasm',
                        'qpeexact_indep_qiskit_10.qasm',
                        'ghz_indep_qiskit_10.qasm',

                        'ae_indep_qiskit_50.qasm',
                        'qft_indep_qiskit_50.qasm',
                        'qpeexact_indep_qiskit_50.qasm',
                        'ghz_indep_qiskit_50.qasm',

                        'ae_indep_qiskit_100.qasm',
                        'qft_indep_qiskit_100.qasm',
                        'qpeexact_indep_qiskit_100.qasm',
                        'ghz_indep_qiskit_100.qasm'
                        ]   
    else:
        # list of circuit files for calibration with 50 and 100 qubits
        circuit_files = [                     
                        'ae_indep_qiskit_50.qasm',
                        'qft_indep_qiskit_50.qasm',
                        'qpeexact_indep_qiskit_50.qasm',
                        'ghz_indep_qiskit_50.qasm',

                        'ae_indep_qiskit_100.qasm',
                        'qft_indep_qiskit_100.qasm',
                        'qpeexact_indep_qiskit_100.qasm',
                        'ghz_indep_qiskit_100.qasm'
                        ]                   
       
    with open(circuit_folder + "\\" + log_file, 'w') as sv:

        # save record in log file
        sv.write("Circuit\t" + "ni\t"+ "ei\t" + "oi\t" + "ri\t" + "pi\t"  + "filename\t" + '\n')  

        #===================================================================================
        # running experiments for each benchmark circuit.
        #===================================================================================
        #
        for circuit_file in circuit_files:

            # loading qasm instructions for the circuit.
            qc = QuantumCircuit.from_qasm_file( circuit_folder + "\\" + circuit_file )    

            # creating the quantum circuit in qasm instructions.
            qc_qasm = qc.qasm()
            
            # converting qasm instructions in hypergraph  
            qc_hypergraph = convert_qasm_in_extended_hypergraph(qc_qasm)

            # partitioning the hypergraph in nparts
            partitions = extended_hypergraph_partition_by_connections(qc_hypergraph,nparts)

            i = 1
            # ------------------------------------------------------------------
            # get statistics from each partition
            for each in partitions:        

                print("create_qasm_files_from_partitions index " + str(i) + " from " + str(nparts))
                print('\n')
                
                # creating n partition files from qasm circuit  
                partition_file = create_qasm_file_from_partition(i, circuit_folder,circuit_file,qc_qasm,nparts,each,kfolder)            
                
                print("partition_file created: ", partition_file)
                print('\n')

                qc_each_file = QuantumCircuit.from_qasm_file(circuit_folder + "\\" + kfolder + "\\" + partition_file)
                pi = qc_each_file.depth()
                print("pi calculated: ",pi)

                qc_each_file_qasm = qc_each_file.qasm()

                # creating the statistics for the qasm circuit
                qc_stats = statistics_from_qasm(qc_each_file_qasm, pi, partition_file)

                print("statistics from the partition qasm file: \n")
                print(qc_stats)
                
                # saving statistics
                sv.write(qc_stats)
               
                i = i + 1
            
            # end for each in partitions
            # ------------------------------------------------------------------

        #
        #===================================================================================

        print('Closing log file: ', log_file)
        sv.close()


In [68]:
random_partition_by_k(15)

def: run_Random_Partition_by_k
Starting process for 15 partitions.

# Creating segment: 1

aux_hg:  {'nodes': ['eval[0]', 'eval[1]', 'eval[2]'], 'edges': [('eval[0]', 'q[0]'), ('eval[0]', 'q[0]'), ('eval[1]', 'q[0]'), ('eval[1]', 'q[0]'), ('eval[2]', 'q[0]'), ('eval[2]', 'q[0]'), ('eval[3]', 'q[0]'), ('eval[3]', 'q[0]'), ('eval[4]', 'q[0]'), ('eval[4]', 'q[0]'), ('eval[5]', 'q[0]'), ('eval[5]', 'q[0]'), ('eval[6]', 'q[0]'), ('eval[6]', 'q[0]'), ('eval[7]', 'q[0]'), ('eval[7]', 'q[0]'), ('eval[8]', 'q[0]'), ('eval[8]', 'q[0]'), ('eval[9]', 'q[0]'), ('eval[9]', 'q[0]'), ('eval[10]', 'q[0]'), ('eval[10]', 'q[0]'), ('eval[11]', 'q[0]'), ('eval[11]', 'q[0]'), ('eval[12]', 'q[0]'), ('eval[12]', 'q[0]'), ('eval[13]', 'q[0]'), ('eval[13]', 'q[0]'), ('eval[14]', 'q[0]'), ('eval[14]', 'q[0]'), ('eval[15]', 'q[0]'), ('eval[15]', 'q[0]'), ('eval[16]', 'q[0]'), ('eval[16]', 'q[0]'), ('eval[17]', 'q[0]'), ('eval[17]', 'q[0]'), ('eval[18]', 'q[0]'), ('eval[18]', 'q[0]'), ('eval[19]', 'q[0]'), ('eval[

don not save barriers tag.
partition_file created:  p3_k15_ae_indep_qiskit_50.qasm


pi calculated:  59
r: 0.9607843137254902
n: 50
circuit_name: ae_50
statistics from the partition qasm file: 

ae_50	50	147	153	0.9607843137254902	59	p3_k15_ae_indep_qiskit_50.qasm

create_qasm_files_from_partitions index 4 from 15


don not save barriers tag.
partition_file created:  p4_k15_ae_indep_qiskit_50.qasm


pi calculated:  59
r: 0.9607843137254902
n: 50
circuit_name: ae_50
statistics from the partition qasm file: 

ae_50	50	147	153	0.9607843137254902	59	p4_k15_ae_indep_qiskit_50.qasm

create_qasm_files_from_partitions index 5 from 15


don not save barriers tag.
partition_file created:  p5_k15_ae_indep_qiskit_50.qasm


pi calculated:  59
r: 0.9607843137254902
n: 50
circuit_name: ae_50
statistics from the partition qasm file: 

ae_50	50	147	153	0.9607843137254902	59	p5_k15_ae_indep_qiskit_50.qasm

create_qasm_files_from_partitions index 6 from 15


don not save barriers tag.
partition_file crea

don not save barriers tag.
partition_file created:  p4_k15_qft_indep_qiskit_50.qasm


pi calculated:  54
r: 0.98
n: 50
circuit_name: qft_50
statistics from the partition qasm file: 

qft_50	50	147	150	0.98	54	p4_k15_qft_indep_qiskit_50.qasm

create_qasm_files_from_partitions index 5 from 15


don not save barriers tag.
partition_file created:  p5_k15_qft_indep_qiskit_50.qasm


pi calculated:  54
r: 0.98
n: 50
circuit_name: qft_50
statistics from the partition qasm file: 

qft_50	50	147	150	0.98	54	p5_k15_qft_indep_qiskit_50.qasm

create_qasm_files_from_partitions index 6 from 15


don not save barriers tag.
partition_file created:  p6_k15_qft_indep_qiskit_50.qasm


pi calculated:  54
r: 0.98
n: 50
circuit_name: qft_50
statistics from the partition qasm file: 

qft_50	50	147	150	0.98	54	p6_k15_qft_indep_qiskit_50.qasm

create_qasm_files_from_partitions index 7 from 15


don not save barriers tag.
partition_file created:  p7_k15_qft_indep_qiskit_50.qasm


pi calculated:  54
r: 0.98
n: 50

pi calculated:  55
r: 0.9607843137254902
n: 50
circuit_name: qpeexact_50
statistics from the partition qasm file: 

qpeexact_50	50	147	153	0.9607843137254902	55	p3_k15_qpeexact_indep_qiskit_50.qasm

create_qasm_files_from_partitions index 4 from 15


don not save barriers tag.
partition_file created:  p4_k15_qpeexact_indep_qiskit_50.qasm


pi calculated:  55
r: 0.9607843137254902
n: 50
circuit_name: qpeexact_50
statistics from the partition qasm file: 

qpeexact_50	50	147	153	0.9607843137254902	55	p4_k15_qpeexact_indep_qiskit_50.qasm

create_qasm_files_from_partitions index 5 from 15


don not save barriers tag.
partition_file created:  p5_k15_qpeexact_indep_qiskit_50.qasm


pi calculated:  55
r: 0.9607843137254902
n: 50
circuit_name: qpeexact_50
statistics from the partition qasm file: 

qpeexact_50	50	147	153	0.9607843137254902	55	p5_k15_qpeexact_indep_qiskit_50.qasm

create_qasm_files_from_partitions index 6 from 15


don not save barriers tag.
partition_file created:  p6_k15_qpeexa

create_qasm_files_from_partitions index 1 from 15


don not save barriers tag.
partition_file created:  p1_k15_ghz_indep_qiskit_50.qasm


pi calculated:  4
r: 1.0
n: 50
circuit_name: ghz_50
statistics from the partition qasm file: 

ghz_50	50	3	3	1.0	4	p1_k15_ghz_indep_qiskit_50.qasm

create_qasm_files_from_partitions index 2 from 15


don not save barriers tag.
partition_file created:  p2_k15_ghz_indep_qiskit_50.qasm


pi calculated:  5
r: 1.0
n: 50
circuit_name: ghz_50
statistics from the partition qasm file: 

ghz_50	50	4	4	1.0	5	p2_k15_ghz_indep_qiskit_50.qasm

create_qasm_files_from_partitions index 3 from 15


don not save barriers tag.
partition_file created:  p3_k15_ghz_indep_qiskit_50.qasm


pi calculated:  5
r: 1.0
n: 50
circuit_name: ghz_50
statistics from the partition qasm file: 

ghz_50	50	4	4	1.0	5	p3_k15_ghz_indep_qiskit_50.qasm

create_qasm_files_from_partitions index 4 from 15


don not save barriers tag.
partition_file created:  p4_k15_ghz_indep_qiskit_50.qasm


pi c

pi calculated:  118
r: 0.9798994974874372
n: 100
circuit_name: ae_100
statistics from the partition qasm file: 

ae_100	100	585	597	0.9798994974874372	118	p1_k15_ae_indep_qiskit_100.qasm

create_qasm_files_from_partitions index 2 from 15


don not save barriers tag.
partition_file created:  p2_k15_ae_indep_qiskit_100.qasm


pi calculated:  118
r: 0.9798994974874372
n: 100
circuit_name: ae_100
statistics from the partition qasm file: 

ae_100	100	585	597	0.9798994974874372	118	p2_k15_ae_indep_qiskit_100.qasm

create_qasm_files_from_partitions index 3 from 15


don not save barriers tag.
partition_file created:  p3_k15_ae_indep_qiskit_100.qasm


pi calculated:  118
r: 0.9798994974874372
n: 100
circuit_name: ae_100
statistics from the partition qasm file: 

ae_100	100	585	597	0.9798994974874372	118	p3_k15_ae_indep_qiskit_100.qasm

create_qasm_files_from_partitions index 4 from 15


don not save barriers tag.
partition_file created:  p4_k15_ae_indep_qiskit_100.qasm


pi calculated:  118
r:

pi calculated:  107
r: 0.9898477157360406
n: 100
circuit_name: qft_100
statistics from the partition qasm file: 

qft_100	100	585	591	0.9898477157360406	107	p1_k15_qft_indep_qiskit_100.qasm

create_qasm_files_from_partitions index 2 from 15


don not save barriers tag.
partition_file created:  p2_k15_qft_indep_qiskit_100.qasm


pi calculated:  107
r: 0.9898477157360406
n: 100
circuit_name: qft_100
statistics from the partition qasm file: 

qft_100	100	585	591	0.9898477157360406	107	p2_k15_qft_indep_qiskit_100.qasm

create_qasm_files_from_partitions index 3 from 15


don not save barriers tag.
partition_file created:  p3_k15_qft_indep_qiskit_100.qasm


pi calculated:  107
r: 0.9898477157360406
n: 100
circuit_name: qft_100
statistics from the partition qasm file: 

qft_100	100	585	591	0.9898477157360406	107	p3_k15_qft_indep_qiskit_100.qasm

create_qasm_files_from_partitions index 4 from 15


don not save barriers tag.
partition_file created:  p4_k15_qft_indep_qiskit_100.qasm


pi calcula

r: 0.9798994974874372
n: 100
circuit_name: qpeexact_100
statistics from the partition qasm file: 

qpeexact_100	100	585	597	0.9798994974874372	108	p1_k15_qpeexact_indep_qiskit_100.qasm

create_qasm_files_from_partitions index 2 from 15


don not save barriers tag.
partition_file created:  p2_k15_qpeexact_indep_qiskit_100.qasm


pi calculated:  108
r: 0.9798994974874372
n: 100
circuit_name: qpeexact_100
statistics from the partition qasm file: 

qpeexact_100	100	585	597	0.9798994974874372	108	p2_k15_qpeexact_indep_qiskit_100.qasm

create_qasm_files_from_partitions index 3 from 15


don not save barriers tag.
partition_file created:  p3_k15_qpeexact_indep_qiskit_100.qasm


pi calculated:  108
r: 0.9798994974874372
n: 100
circuit_name: qpeexact_100
statistics from the partition qasm file: 

qpeexact_100	100	585	597	0.9798994974874372	108	p3_k15_qpeexact_indep_qiskit_100.qasm

create_qasm_files_from_partitions index 4 from 15


don not save barriers tag.
partition_file created:  p4_k15_qpe

pi calculated:  7
r: 1.0
n: 100
circuit_name: ghz_100
statistics from the partition qasm file: 

ghz_100	100	6	6	1.0	7	p1_k15_ghz_indep_qiskit_100.qasm

create_qasm_files_from_partitions index 2 from 15


don not save barriers tag.
partition_file created:  p2_k15_ghz_indep_qiskit_100.qasm


pi calculated:  8
r: 1.0
n: 100
circuit_name: ghz_100
statistics from the partition qasm file: 

ghz_100	100	7	7	1.0	8	p2_k15_ghz_indep_qiskit_100.qasm

create_qasm_files_from_partitions index 3 from 15


don not save barriers tag.
partition_file created:  p3_k15_ghz_indep_qiskit_100.qasm


pi calculated:  8
r: 1.0
n: 100
circuit_name: ghz_100
statistics from the partition qasm file: 

ghz_100	100	7	7	1.0	8	p3_k15_ghz_indep_qiskit_100.qasm

create_qasm_files_from_partitions index 4 from 15


don not save barriers tag.
partition_file created:  p4_k15_ghz_indep_qiskit_100.qasm


pi calculated:  8
r: 1.0
n: 100
circuit_name: ghz_100
statistics from the partition qasm file: 

ghz_100	100	7	7	1.0	8	p4_k1